### function to calculate minimum probility p_min to check given condition

In [12]:
def p_minimum(n,trail_cap,B_cap,B_bar):
        p_min = 1.0;
        for i in range(0,n):
            p_min *= trail_cap[i].wt
        p_min = p_min * B_cap[nrounds - 1 - (n + 1)]; 
        p_min = B_bar/p_min
        #print(B_bar,p_min)
        return p_min

### function to check given inputs are available in highways path list or not 

In [13]:
def highwaylist():
    alph,bet,gam,pro = [],[],[],[]
    with open('alph.txt') as ip1, open('bet.txt') as ip2, open('gam.txt') as ip3, open('pro.txt') as ip4:
        for i1,i2,i3,i4 in zip(ip1,ip2,ip3,ip4):
            hw.append(NMTS(int(i1.strip()),int(i2.strip()),int(i3.strip()),float(i4.strip()))) 
            

### function to calculate weight 

In [14]:
def weight(alpha1,beta1,gamma1): 
    x1= (alpha1 << 1)& mask
    y1= (beta1  << 1)& mask
    z1= (gamma1  << 1)& mask
    not_x=(x1^mask)
    eq=((not_x)^y1)&(not_x^z1)
    s=eq&(alpha1^beta1^gamma1^(y1))
    if(s==0):        
        h=bin((~eq)& mask)
        wt=(h[1:].count("1"))
        return math.pow(2,-wt)
    else:
        return -200

In [15]:
##fucntion to find output for which weight is max

In [16]:
def PDDT(n,p_thres,k,wt,da,db,dc,s,maxddt,ddt,m):
    if(n==k):
        ddt.append(NMTS(da,db,dc,wt))
        if(wt>=s):
            maxddt.append(NMTS(da,db,dc,wt))
        return 
    
    for z in range(0,2):
        new_da= (da & ((2 ** m) - 1))
        new_db= (db & ((2 ** m) - 1))
        new_dc= (dc | (z<<k) & mask)
        wt= weight(new_da,new_db,new_dc)
        if(wt >= p_thres or ((z==1) and (k+1)!=n)):                    
            PDDT(n,p_thres,k+1,wt,da,db,new_dc,s,maxddt,ddt,m+1)  
            
    if(len(ddt)==0):
        return 0,ddt,maxddt
    else:
        return 1,ddt,maxddt
   

### function to perform left and right circular rotation 

In [17]:

#right circular shifts
def ROR(x,r):
    x = ((x << (SPECK_TYPE - r)) + (x >> r)) & mask
    return x

#left circular shifts
def ROL(x,r):
    x = ((x >> (SPECK_TYPE - r)) + (x << r)) & mask
    return x

### main function for threshold search

In [24]:
def threshold_search(n,nrounds,hw,B_cap,B_bar,B_barlist,st0,st1,op,w1):
    if(n == 0): 
        B_cap_temp[nrounds-1]=w1*B_cap[nrounds-1-(n+1)]
        if(B_cap_temp[nrounds-1]>B_bar):
            B_barlist[n]=w1
            trail_cap[n]= NMTS(ROL(st1,alpha),st0,op,w1)
            st1=op
            st0=ROL(st0,beta)^st1
            return threshold_search(n+1,nrounds,hw,B_cap,B_bar,B_barlist,st0,st1,op,w1)
        else:
            return B_bar,B_cap 
            
    if((n > 0) & (n != (nrounds - 1))):
        #print(n)
        st1=ROR(st1,alpha)
        p_min=p_minimum(n,trail_cap,B_cap,B_bar)
        croad=[]
        #function that check output is in highway and weight is greater than p_min or not, if it is update croad
        maxddt,ddt,max_p=[],[],0
        ck,ddt,maxddt=PDDT(SPECK_TYPE,0.05,0,1,st1,st0,0,p_min,maxddt,ddt,1)
        if(len(maxddt)!=0):
            for i in range(0,len(maxddt)):
                croad.append(NMTS(maxddt[i].dx,maxddt[i].dy,maxddt[i].dz,maxddt[i].wt))           
        #opcheck_in_highways(0,p_min,st1,st0)
        #if croad is still empty then fill it with max probility value for other outputs except highway
        if(len(croad) == 0):
            maxop=st1^st0
            maxwt=weight(st1,st0,maxop)
            if(maxwt!= -200):
                croad.append(NMTS(st1,st0,maxop,maxwt))
            else:
                return B_bar,B_cap
    
        crhw = []
        temphw=[]
        maxddt,ddt,max_p=[],[],0
        ck,ddt,maxddt=PDDT(SPECK_TYPE,0.05,0,1,st1,st0,0,max_p,maxddt,ddt,1)
        #val1,val2,val3,w,chk= searchinhighway(st1,st0)
        if(ck==1):
            for i in range(0,len(ddt)):
                crhw.append(NMTS(ddt[i].dx,ddt[i].dy,ddt[i].dz,ddt[i].wt))
        
        for i in range(0,len(croad)):
            crhw.append(NMTS(croad[i].dx,croad[i].dy,croad[i].dz,croad[i].wt))
   
        p_r=1
        for i in range(0,n):
            p_r *= trail_cap[i].wt
        for i in range(0,len(crhw)):
            B_cap_temp[nrounds-1]= p_r * crhw[i].wt * B_cap[nrounds - 1 - (n + 1)]
            #print(B_cap_temp[nrounds-1],B_bar)
            if(B_cap_temp[nrounds-1]>B_bar):
                B_barlist[n]=p_r * crhw[i].wt
                trail_cap[n]=NMTS(ROL(crhw[i].dx,alpha),crhw[i].dy,crhw[i].dz,crhw[i].wt)
                st1=crhw[i].dz
                st0=ROL(st0,beta)^st1
                return threshold_search(n+1,nrounds,hw,B_cap,B_bar,B_barlist,st0,st1,op,w1)
            else:
                return B_bar,B_cap
        
                    
    if(n ==(nrounds - 1)):
        st1=ROR(st1,alpha)
        #print(n)
        #max_p,output,ck=max(0,st1,st0)
        maxop=st1^st0
        maxwt=weight(st1,st0,maxop)
        if(maxwt>0):
            p=maxwt
            op=maxop
            if(p>=0.05):
                hw.append(NMTS(st1,st0,op,p))       
        if(maxwt==-200):
            return B_bar,B_cap             
        p_r=1
        for i in range(0,n):
            p_r *= trail_cap[i].wt
        B_cap_temp[nrounds-1]=p * p_r
        #print(B_cap_temp[nrounds-1],B_bar)
        if(B_cap_temp[nrounds-1]>B_bar):
            B_barlist[n]=B_cap_temp[nrounds-1]
            #print ("%.16f %.16f" % (B_cap_temp[n],B_bar))
            trail_cap[n]=NMTS(ROL(st1,alpha),st0,op,p)
            B_bar=B_cap_temp[nrounds-1]
            for i in range(0,len(B_cap)):
                B_cap[i]=B_barlist[i]
                B_bar=B_cap_temp[n]  
            for i in range(0,len(trail_cap)):
                print(trail_cap[i].dx,trail_cap[i].dy,trail_cap[i].dz,trail_cap[i].wt)
            print(B_bar)
            print()
            return B_bar,B_cap
        else:
            return B_bar,B_cap
    

In [ ]:
import random
import math 
#alpha beta are for left and right circular shift     
alpha, beta = 7,2
#speck total number of round epresented by nrounds
nrounds,n,s=9,0,0
SPECK_TYPE=16
mask,wshift = 2 ** 16 - 1, 15
#B_cap,B_bar=[0.00048,0.00048,0.0625,0.00048,0.00048,0.00048,0.00048,0.00048,0.00048],1.7763568394002505e-15
B_cap,B_bar=[2**(-11),2**(-22),2**(-33),2**(-38),2**(-49),2**(-60),2**(-71),2**(-82),2**(-91)],2 ** (-91)
B_barlist=[0]*nrounds
#B_cap,B_bar=[2**(-11),2**(-22),2**(-33),2**(-38)],2 ** (-38)
trail_cap,trail_bar=[0]*nrounds, [0]*nrounds
croad,hw,B_cap_temp=[],[],[0]*nrounds
#st0=0xA60
#st1=0x4205
max_p,output=0,0
maxddt,ddt,max_p=[],[],0
print ("%.30f" % B_bar)
class NMTS(object):
    """__init__() functions as the class constructor"""
    def __init__(self, dx=None, dy=None, dz=None, wt=None):
        self.dx = dx
        self.dy = dy
        self.dz = dz
        self.wt = wt
        
highwaylist()
for ch in range(0,len(hw)):
    #print(n,nrounds,B_bar,hw[ch].dx,hw[ch].dy,hw[ch].dz,hw[ch].wt)
    B_bar,B_cap =threshold_search(n,nrounds,hw,B_cap,B_bar,B_barlist,hw[ch].dx,hw[ch].dy,hw[ch].dz,hw[ch].wt)
    print(B_bar,ch)

0.000000000000000000000000000404
64 0 32768 1.0
32768 32768 33024 0.5
33024 33026 32768 0.25
32768 33802 34058 0.0625
34058 38176 32810 0.015625
32810 54440 33192 0.0078125
33192 54027 33288 0.0078125
33288 52775 57123 0.0009765625
57123 59324 40962 0.00048828125
3.552713678800501e-15

3.552713678800501e-15 0
3.552713678800501e-15 1
3.552713678800501e-15 2
3.552713678800501e-15 3
3.552713678800501e-15 4
3.552713678800501e-15 5
3.552713678800501e-15 6
3.552713678800501e-15 7
3.552713678800501e-15 8
3.552713678800501e-15 9
3.552713678800501e-15 10
3.552713678800501e-15 11
3.552713678800501e-15 12
3.552713678800501e-15 13
3.552713678800501e-15 14
3.552713678800501e-15 15
3.552713678800501e-15 16
3.552713678800501e-15 17
3.552713678800501e-15 18
3.552713678800501e-15 19
3.552713678800501e-15 20
3.552713678800501e-15 21
3.552713678800501e-15 22
3.552713678800501e-15 23
3.552713678800501e-15 24
3.552713678800501e-15 25
3.552713678800501e-15 26
3.552713678800501e-15 27
3.552713678800501e-15 2

1.4210854715202004e-14 296
1.4210854715202004e-14 297
1.4210854715202004e-14 298
1.4210854715202004e-14 299
1.4210854715202004e-14 300
1.4210854715202004e-14 301
1.4210854715202004e-14 302
1.4210854715202004e-14 303
1.4210854715202004e-14 304
1.4210854715202004e-14 305
1.4210854715202004e-14 306
1.4210854715202004e-14 307
1.4210854715202004e-14 308
1.4210854715202004e-14 309
1.4210854715202004e-14 310
1.4210854715202004e-14 311
1.4210854715202004e-14 312
1.4210854715202004e-14 313
1.4210854715202004e-14 314
1.4210854715202004e-14 315
1.4210854715202004e-14 316
1.4210854715202004e-14 317
1.4210854715202004e-14 318
1.4210854715202004e-14 319
1.4210854715202004e-14 320
1.4210854715202004e-14 321
1.4210854715202004e-14 322
1.4210854715202004e-14 323
1.4210854715202004e-14 324
1.4210854715202004e-14 325
1.4210854715202004e-14 326
1.4210854715202004e-14 327
1.4210854715202004e-14 328
1.4210854715202004e-14 329
1.4210854715202004e-14 330
1.4210854715202004e-14 331
1.4210854715202004e-14 332
1

1.4210854715202004e-14 606
1.4210854715202004e-14 607
1.4210854715202004e-14 608
1.4210854715202004e-14 609
1.4210854715202004e-14 610
1.4210854715202004e-14 611
1.4210854715202004e-14 612
1.4210854715202004e-14 613
1.4210854715202004e-14 614
1.4210854715202004e-14 615
1.4210854715202004e-14 616
1.4210854715202004e-14 617
1.4210854715202004e-14 618
1.4210854715202004e-14 619
1.4210854715202004e-14 620
1.4210854715202004e-14 621
1.4210854715202004e-14 622
1.4210854715202004e-14 623
1.4210854715202004e-14 624
1.4210854715202004e-14 625
1.4210854715202004e-14 626
1.4210854715202004e-14 627
1.4210854715202004e-14 628
1.4210854715202004e-14 629
1.4210854715202004e-14 630
1.4210854715202004e-14 631
1.4210854715202004e-14 632
1.4210854715202004e-14 633
1.4210854715202004e-14 634
1.4210854715202004e-14 635
1.4210854715202004e-14 636
1.4210854715202004e-14 637
1.4210854715202004e-14 638
1.4210854715202004e-14 639
1.4210854715202004e-14 640
1.4210854715202004e-14 641
1.4210854715202004e-14 642
1

1.4210854715202004e-14 917
1.4210854715202004e-14 918
1.4210854715202004e-14 919
1.4210854715202004e-14 920
1.4210854715202004e-14 921
1.4210854715202004e-14 922
1.4210854715202004e-14 923
1.4210854715202004e-14 924
1.4210854715202004e-14 925
1.4210854715202004e-14 926
1.4210854715202004e-14 927
1.4210854715202004e-14 928
1.4210854715202004e-14 929
1.4210854715202004e-14 930
1.4210854715202004e-14 931
1.4210854715202004e-14 932
1.4210854715202004e-14 933
1.4210854715202004e-14 934
1.4210854715202004e-14 935
1.4210854715202004e-14 936
1.4210854715202004e-14 937
1.4210854715202004e-14 938
1.4210854715202004e-14 939
1.4210854715202004e-14 940
1.4210854715202004e-14 941
1.4210854715202004e-14 942
1.4210854715202004e-14 943
1.4210854715202004e-14 944
1.4210854715202004e-14 945
1.4210854715202004e-14 946
1.4210854715202004e-14 947
1.4210854715202004e-14 948
1.4210854715202004e-14 949
1.4210854715202004e-14 950
1.4210854715202004e-14 951
1.4210854715202004e-14 952
1.4210854715202004e-14 953
1

2.842170943040401e-14 1221
2.842170943040401e-14 1222
2.842170943040401e-14 1223
2.842170943040401e-14 1224
2.842170943040401e-14 1225
2.842170943040401e-14 1226
2.842170943040401e-14 1227
2.842170943040401e-14 1228
2.842170943040401e-14 1229
2.842170943040401e-14 1230
2.842170943040401e-14 1231
2.842170943040401e-14 1232
2.842170943040401e-14 1233
2.842170943040401e-14 1234
2.842170943040401e-14 1235
2.842170943040401e-14 1236
2.842170943040401e-14 1237
2.842170943040401e-14 1238
2.842170943040401e-14 1239
2.842170943040401e-14 1240
2.842170943040401e-14 1241
2.842170943040401e-14 1242
2.842170943040401e-14 1243
2.842170943040401e-14 1244
2.842170943040401e-14 1245
2.842170943040401e-14 1246
2.842170943040401e-14 1247
2.842170943040401e-14 1248
2.842170943040401e-14 1249
2.842170943040401e-14 1250
2.842170943040401e-14 1251
2.842170943040401e-14 1252
2.842170943040401e-14 1253
2.842170943040401e-14 1254
2.842170943040401e-14 1255
2.842170943040401e-14 1256
2.842170943040401e-14 1257
2

...

2.9103830456733704e-11 119952
2.9103830456733704e-11 119953
2.9103830456733704e-11 119954
2.9103830456733704e-11 119955
2.9103830456733704e-11 119956
2.9103830456733704e-11 119957
2.9103830456733704e-11 119958
2.9103830456733704e-11 119959
2.9103830456733704e-11 119960
2.9103830456733704e-11 119961
2.9103830456733704e-11 119962
2.9103830456733704e-11 119963
2.9103830456733704e-11 119964
2.9103830456733704e-11 119965
2.9103830456733704e-11 119966
2.9103830456733704e-11 119967
2.9103830456733704e-11 119968
2.9103830456733704e-11 119969
2.9103830456733704e-11 119970
2.9103830456733704e-11 119971
2.9103830456733704e-11 119972
2.9103830456733704e-11 119973
2.9103830456733704e-11 119974
2.9103830456733704e-11 119975
2.9103830456733704e-11 119976
2.9103830456733704e-11 119977
2.9103830456733704e-11 119978
2.9103830456733704e-11 119979
2.9103830456733704e-11 119980
2.9103830456733704e-11 119981
2.9103830456733704e-11 119982
2.9103830456733704e-11 119983
2.9103830456733704e-11 119984
2.91038304

2.9103830456733704e-11 120274
2.9103830456733704e-11 120275
2.9103830456733704e-11 120276
2.9103830456733704e-11 120277
2.9103830456733704e-11 120278
2.9103830456733704e-11 120279
2.9103830456733704e-11 120280
2.9103830456733704e-11 120281
2.9103830456733704e-11 120282
2.9103830456733704e-11 120283
2.9103830456733704e-11 120284
2.9103830456733704e-11 120285
2.9103830456733704e-11 120286
2.9103830456733704e-11 120287
2.9103830456733704e-11 120288
2.9103830456733704e-11 120289
2.9103830456733704e-11 120290
2.9103830456733704e-11 120291
2.9103830456733704e-11 120292
2.9103830456733704e-11 120293
2.9103830456733704e-11 120294
2.9103830456733704e-11 120295
2.9103830456733704e-11 120296
2.9103830456733704e-11 120297
2.9103830456733704e-11 120298
2.9103830456733704e-11 120299
2.9103830456733704e-11 120300
2.9103830456733704e-11 120301
2.9103830456733704e-11 120302
2.9103830456733704e-11 120303
2.9103830456733704e-11 120304
2.9103830456733704e-11 120305
2.9103830456733704e-11 120306
2.91038304

2.9103830456733704e-11 120599
2.9103830456733704e-11 120600
2.9103830456733704e-11 120601
2.9103830456733704e-11 120602
2.9103830456733704e-11 120603
2.9103830456733704e-11 120604
2.9103830456733704e-11 120605
2.9103830456733704e-11 120606
2.9103830456733704e-11 120607
2.9103830456733704e-11 120608
2.9103830456733704e-11 120609
2.9103830456733704e-11 120610
2.9103830456733704e-11 120611
2.9103830456733704e-11 120612
2.9103830456733704e-11 120613
2.9103830456733704e-11 120614
2.9103830456733704e-11 120615
2.9103830456733704e-11 120616
2.9103830456733704e-11 120617
2.9103830456733704e-11 120618
2.9103830456733704e-11 120619
2.9103830456733704e-11 120620
2.9103830456733704e-11 120621
2.9103830456733704e-11 120622
2.9103830456733704e-11 120623
2.9103830456733704e-11 120624
2.9103830456733704e-11 120625
2.9103830456733704e-11 120626
2.9103830456733704e-11 120627
2.9103830456733704e-11 120628
2.9103830456733704e-11 120629
2.9103830456733704e-11 120630
2.9103830456733704e-11 120631
2.91038304

2.9103830456733704e-11 120873
2.9103830456733704e-11 120874
2.9103830456733704e-11 120875
2.9103830456733704e-11 120876
2.9103830456733704e-11 120877
2.9103830456733704e-11 120878
2.9103830456733704e-11 120879
2.9103830456733704e-11 120880
2.9103830456733704e-11 120881
2.9103830456733704e-11 120882
2.9103830456733704e-11 120883
2.9103830456733704e-11 120884
2.9103830456733704e-11 120885
2.9103830456733704e-11 120886
2.9103830456733704e-11 120887
2.9103830456733704e-11 120888
2.9103830456733704e-11 120889
2.9103830456733704e-11 120890
2.9103830456733704e-11 120891
2.9103830456733704e-11 120892
2.9103830456733704e-11 120893
2.9103830456733704e-11 120894
2.9103830456733704e-11 120895
2.9103830456733704e-11 120896
2.9103830456733704e-11 120897
2.9103830456733704e-11 120898
2.9103830456733704e-11 120899
2.9103830456733704e-11 120900
2.9103830456733704e-11 120901
2.9103830456733704e-11 120902
2.9103830456733704e-11 120903
2.9103830456733704e-11 120904
2.9103830456733704e-11 120905
2.91038304

2.9103830456733704e-11 121225
2.9103830456733704e-11 121226
2.9103830456733704e-11 121227
2.9103830456733704e-11 121228
2.9103830456733704e-11 121229
2.9103830456733704e-11 121230
2.9103830456733704e-11 121231
2.9103830456733704e-11 121232
2.9103830456733704e-11 121233
2.9103830456733704e-11 121234
2.9103830456733704e-11 121235
2.9103830456733704e-11 121236
2.9103830456733704e-11 121237
2.9103830456733704e-11 121238
2.9103830456733704e-11 121239
2.9103830456733704e-11 121240
2.9103830456733704e-11 121241
2.9103830456733704e-11 121242
2.9103830456733704e-11 121243
2.9103830456733704e-11 121244
2.9103830456733704e-11 121245
2.9103830456733704e-11 121246
2.9103830456733704e-11 121247
2.9103830456733704e-11 121248
2.9103830456733704e-11 121249
2.9103830456733704e-11 121250
2.9103830456733704e-11 121251
2.9103830456733704e-11 121252
2.9103830456733704e-11 121253
2.9103830456733704e-11 121254
2.9103830456733704e-11 121255
2.9103830456733704e-11 121256
2.9103830456733704e-11 121257
2.91038304